In [16]:
import optuna
from sklearn import datasets
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import cross_val_score
from optuna.pruners import SuccessiveHalvingPruner
from optuna.samplers import TPESampler, HilbertSampler, RandomSampler, GridSampler
import numpy as np

def objective(trial):
    digits = datasets.load_digits()
    X, y = digits.data, digits.target

    max_depth = trial.suggest_float("rf_max_depth", 2, 64)#, log=True)
    max_samples = trial.suggest_float("rf_max_samples", 0.2, 1)
    n_estimators = trial.suggest_float("n_estimators", 10, 100)
   
    rf_model = RandomForestClassifier(
        max_depth = int(max_depth),
        max_samples = max_samples,
        n_estimators = int(n_estimators),
        random_state = 42)
    
    score = cross_val_score(rf_model, X, y,  cv=3).mean()
    return score

from optuna.samplers import TPESampler, HilbertSampler, RandomSampler, GridSampler

#search_space = {"rf_max_depth": np.linspace(2, 64, 10), "rf_max_samples": np.linspace(0.2, 1.0, 10)}

n_trials = 200
search_space = {"rf_max_depth": [2, 64], "rf_max_samples": [0.2, 1], "n_estimators": [10, 100]}
hilbert = optuna.create_study(direction = "maximize", sampler = HilbertSampler(search_space, n_trials, seed=42))
hilbert.optimize(objective, n_trials)

random = optuna.create_study(direction = "maximize", sampler = RandomSampler())
random.optimize(objective, n_trials)

tpe = optuna.create_study(direction = "maximize", sampler = TPESampler())
tpe.optimize(objective, n_trials)


[I 2023-10-27 21:37:45,375] A new study created in memory with name: no-name-b3b8940d-da7d-46fb-a3b0-24c428766235
[I 2023-10-27 21:37:45,550] Trial 0 finished with value: 0.9309961046188091 and parameters: {'rf_max_depth': 55.14285714285714, 'rf_max_samples': 0.7714285714285716, 'n_estimators': 40.0}. Best is trial 0 with value: 0.9309961046188091.
[I 2023-10-27 21:37:45,786] Trial 1 finished with value: 0.9198664440734557 and parameters: {'rf_max_depth': 10.857142857142856, 'rf_max_samples': 0.2, 'n_estimators': 100.0}. Best is trial 0 with value: 0.9309961046188091.
[I 2023-10-27 21:37:45,960] Trial 2 finished with value: 0.9271007234279355 and parameters: {'rf_max_depth': 19.71428571428571, 'rf_max_samples': 0.8857142857142857, 'n_estimators': 40.0}. Best is trial 0 with value: 0.9309961046188091.
[I 2023-10-27 21:37:46,206] Trial 3 finished with value: 0.9387868670005565 and parameters: {'rf_max_depth': 28.57142857142857, 'rf_max_samples': 0.5428571428571429, 'n_estimators': 70.0}.

In [17]:
hilbert.best_trial.value, random.best_trial.value, tpe.best_trial.value

(0.941569282136895, 0.9476905954368391, 0.9482470784641069)

In [18]:
optuna.visualization.plot_contour(hilbert)

In [19]:
optuna.visualization.plot_contour(random)

In [20]:
optuna.visualization.plot_contour(tpe)

(0.9387868670005565, 0.941569282136895, 0.9426822481914302)